# GeoSpatial Data Project - Blasi

TODO's

You recently created a new company in the GAMING industry. The company will have the following scheme:

    20 Designers
    5 UI/UX Engineers
    10 Frontend Developers
    15 Data Engineers
    5 Backend Developers
    20 Account Managers
    1 Maintenance guy that loves basketball
    10 Executives
    1 CEO/President.

As a data engineer you have asked all the employees to show their preferences on where to place the new office. Your goal is to place the new company offices in the best place for the company to grow. You have to find a place that more or less covers all the following requirements (note that it's impossible to cover all requirements, so you have to prioritize at your glance):

    Designers like to go to design talks and share knowledge. There must be some nearby companies that also do design.
    30% of the company staff have at least 1 child.
    Developers like to be near successful tech startups that have raised at least 1 Million dollars.
    Executives like Starbucks A LOT. Ensure there's a starbucks not too far.
    Account managers need to travel a lot.
    Everyone in the company is between 25 and 40, give them some place to go party.
    The CEO is vegan.
    If you want to make the maintenance guy happy, a basketball stadium must be around 10 Km.
    The office dog—"Dobby" needs a hairdresser every month. Ensure there's one not too far away.


In [1316]:
import requests
import json
import pandas as pd
import numpy as np
from getpass import getpass
import re 

import os
from dotenv import load_dotenv

from pymongo import MongoClient
import collections

import folium
from folium import Choropleth, Circle, Marker, Icon, Map
from folium.plugins import HeatMap, MarkerCluster
import pandas as pd

import math
import warnings
warnings.filterwarnings("ignore")



In [1317]:
load_dotenv() 

True

In [1318]:
employees = ['Designers',' UI/UX Engineers','Frontend Developers','Data Engineers','Backend Developers','Account Managers','Maintenance','Executives',	'CEO/President']
q_employees = [20,	5,	10,	15,	5,	20,	1,	10,	1]

employee_dict = {
    "emp_type":employees,
    "q_emp":q_employees

}
emp = pd.DataFrame(employee_dict)

emp["%_total"] = (emp['q_emp'] / emp['q_emp'].sum())

employee_perc = emp.sort_values("q_emp",ascending=False)
employee_perc

emp_type  q_emp   %_total
0            Designers     20  0.229885
5     Account Managers     20  0.229885
3       Data Engineers     15  0.172414
2  Frontend Developers     10  0.114943
7           Executives     10  0.114943
1      UI/UX Engineers      5  0.057471
4   Backend Developers      5  0.057471
6          Maintenance      1  0.011494
8        CEO/President      1  0.011494

    Designers: There must be some nearby companies that also do design --> (Company db) design tags
    Developers : Near startups with more than 1M raised -->(Company db) total_money_raised (non numeric format)
    30% of the company staff have at least 1 child. Schools/daycares  (API)
    Executives: Starbucks --> (API)name starbucks
    Account managers: Airport --> (API) name airport
    ALL: party place -->(API) tag party, club?
    CEO: Vegan restaurant --> (API) tag
    maintenance: basketball stadium must be around 10 Km.  --> (API) tag
    The office dog—"Dobby" needs a hairdresser every month. Ensure there's one not too far away.  --> (API) tag

## Companies DB - Mongo

In [1319]:
client = MongoClient("localhost:27017")
client.list_database_names()
db = client["ironhack"]
c = db.get_collection("companies")

In [1373]:
#c.distinct("category_code")

In [1321]:
filter = {"tag_list": {"$regex": "(design|games_video|software|web|internet|digital|gaming|games|animation|UX|UI)"}} 
projection ={"name": 1, "offices":1,"tag_list":1,"total_money_raised":1}

pipeline = [
    {"$match": filter},
    {"$project": projection},
    {"$unwind": "$offices"}
]

complete_dict = list(c.aggregate(pipeline))

In [1322]:
comp_id = [str(complete_dict[i]["_id"]) for i in range(len(complete_dict))]
comp_name = [complete_dict[i]["name"] for i in range(len(complete_dict))]
comp_city = [complete_dict[i]["offices"]["city"] for i in range(len(complete_dict))]
comp_country = [complete_dict[i]["offices"]["country_code"] for i in range(len(complete_dict))]
comp_money_raised = [complete_dict[i]["total_money_raised"] for i in range(len(complete_dict))]
comp_tags = [complete_dict[i]["tag_list"]for i in range(len(complete_dict))]
comp_office_lat = [complete_dict[i]["offices"]["latitude"] for i in range(len(complete_dict))]
comp_office_lon = [complete_dict[i]["offices"]["longitude"] for i in range(len(complete_dict))]



comp_dict= pd.DataFrame({
    "id": comp_id,
    "name" : comp_name,
    "city" : comp_city,
    "country" : comp_country,
    "funds_raised" : comp_money_raised,
    "tags": comp_tags,
    "office_lat": comp_office_lat,
    "office_lon":comp_office_lon
})

comp_df =pd.DataFrame(comp_dict)




### funds raised adjustments

In [1323]:


def convert_value(value):

    amount = float(re.sub(r'[^\d.]', '', value))
    unit = value[-1]

    if unit == 'M':
        amount *= 1000000
    elif unit == 'B':
        amount *= 1000000000
    elif unit == 'k':
        amount *= 1000
    else:
        amount
        
    return amount



In [1324]:
comp_df["funds_raised_float"] = comp_df["funds_raised"].apply(lambda x: convert_value(x))
comp_df["currency"] = comp_df["funds_raised"].apply(lambda x: x[0])
comp_df

id       name           city country funds_raised  \
0     52cdef7c4bab8bd675297d8d       Digg  San Francisco     USA         $45M   
1     52cdef7c4bab8bd675297d97     Scribd  San Francisco     USA       $25.8M   
2     52cdef7c4bab8bd675297da0   Babelgum         London     GBR       $13.2M   
3     52cdef7c4bab8bd675297da3     Yahoo!      Sunnyvale     USA        $6.8M   
4     52cdef7c4bab8bd675297da7    AddThis         Vienna     USA         $73M   
...                        ...        ...            ...     ...          ...   
3902  52cdef7f4bab8bd67529c6d4  Treehouse       Portland     USA       $19.4M   
3903  52cdef7f4bab8bd67529c6dc  acrossair         London     GBR           $0   
3904  52cdef7f4bab8bd67529c6e4     Getyoo       Brussels     BEL       €1.13M   
3905  52cdef7f4bab8bd67529c6f5     Oriact     KÃ¼ssnacht     CHE           $0   
3906  52cdef7f4bab8bd67529c6f6     Adhunk        Bikaner     IND           $0   

                                                   tags  office_lat  \
0     community, social, news, bookmark, digg, techn...   37.764726   
1     book-subscription, digital-library, netflix-fo...   37.789634   
2                                     iptv, web2ireland   53.344104   
3                       search, portal, webmail, photos   37.418531   
4     sharing, social-applications, social-media, an...   38.926172   
...                                                 ...         ...   
3902  online-education, education, programming, web-...         NaN   
3903                   iphone, games, augmented-reality   51.517742   
3904  social-networks, networking, web, real-life, w...   50.839970   
3905  collaboration, communication, appliance, softw...   47.088219   
3906  adhunk, advertiseing, adhunk-publishers, web-p...         NaN   

      office_lon  funds_raised_float currency  
0    -122.394523          45000000.0        $  
1    -122.404052          25800000.0        $  
2      -6.267494          13200000.0        $  
3    -122.025485           6800000.0        $  
4     -77.245195          73000000.0        $  
...          ...                 ...      ...  
3902         NaN          19400000.0        $  
3903   -0.116537                 0.0        $  
3904    4.346472           1130000.0        €  
3905    8.437163                 0.0        $  
3906         NaN                 0.0        $  

[3907 rows x 10 columns]

In [1325]:
ccy = pd.DataFrame({
"sym" : ['$', '€', '£', '¥'],
"fx_rate" : [1,1.07,1.21,0.0076]
})


comp_df = comp_df.merge(ccy,how="left", left_on="currency", right_on="sym")

comp_df["funds_raised_usd"] = comp_df["funds_raised_float"]*comp_df["fx_rate"] # USD equivalent of funds raised
comp_df["desing_tag"] = comp_df["tags"].apply(lambda x: "design" in x) # design tag boolean
comp_df["gaming_tag"] = comp_df["tags"].apply(lambda x: "gaming" in x) # gaming tag boolean
comp_df["funding_tag"] = comp_df["funds_raised_usd"].apply(lambda x: x>1000000) # funding 1M tag





In [1326]:
comp_df.drop(["funds_raised","sym","id"],axis=1,inplace=True) # dropping unnecesary columns
comp_df = comp_df[~comp_df["office_lat"].isna()] # filtering for offices with coordinates
comp_df = comp_df.drop_duplicates() #dropping duplicates

## Analysis

- san francisco, London and NY look promising taking into account design firms and startups with more than USD 1M raised

In [1374]:
pd.DataFrame(comp_df[["country","city"]][comp_df["funds_raised_usd"]>1000000].value_counts()).head(5) #Q companies with more than USD 1M Raised funds

0
country city             
USA     San Francisco  62
        New York       34
GBR     London         25
USA     Austin         14
        Sunnyvale      12

In [1375]:
pd.DataFrame(comp_df[["country","city"]][comp_df["desing_tag"]==True].value_counts()).head(5) #Q companies with design tag

0
country city             
USA     New York       17
GBR     London         14
USA     San Francisco   9
        Los Angeles     9
        San Diego       8

## Choosing one company from each city, with around 1M usd funds raised, assumed comparable/Stealable location

In [1330]:
comp_df[(comp_df["city"]=="London")&(comp_df["gaming_tag"]==True)].sort_values("funds_raised_float")

name    city country  \
529  ExitReality  London     GBR   
858      Vigster  London     GBR   
399        Pikum  London     GBR   
333     Playfish  London     GBR   

                                                  tags  office_lat  \
529  im, virtualworld, metaverse, children, fun, ga...   51.500152   
858  gaming, social-network, community, video-gamin...   51.500152   
399  gaming, social-networks, first-round-capital, ...   51.539778   
333  social-gaming, social-games, social-networks, ...   51.499109   

     office_lon  funds_raised_float currency  fx_rate  funds_raised_usd  \
529   -0.126236                 0.0        $     1.00               0.0   
858   -0.126236             50000.0        £     1.21           60500.0   
399   -0.152998           5920000.0        $     1.00         5920000.0   
333   -0.198480          21000000.0        $     1.00        21000000.0   

     desing_tag  gaming_tag  funding_tag  
529       False        True        False  
858       False        True        False  
399       False        True         True  
333       False        True         True

Vigster 

In [1331]:
comp_df[(comp_df["city"]=="San Francisco")&(comp_df["gaming_tag"]==True)].sort_values("funds_raised_float")

name           city country  \
916      AdParlor  San Francisco     USA   
1070     Scavenja  San Francisco     USA   
1432       plaYce  San Francisco     USA   
1950      GotGame  San Francisco     USA   
1500      Lolapps  San Francisco     USA   
99    Crunchyroll  San Francisco     USA   
2690    CyberArts  San Francisco     USA   
41        Grockit  San Francisco     USA   
1263       ngmoco  San Francisco     USA   
1941       Booyah  San Francisco     USA   

                                                   tags  office_lat  \
916   advertising, facebook, advertising-on-facebook...   37.788660   
1070  scavenger-hunt, gaming, game, photo, picture, ...   37.780134   
1432  techcrunch50, tc50, gaming, virtual-world, mir...   37.802040   
1950  games, video-games, videos, gaming-videos, new...   37.777720   
1500  games, ravenwood-fair, facebook, user-generate...   37.787092   
99    crunchyroll, anime, manga, video, gaming, musi...   37.781265   
2690   poker-gaming-platform-backgammon-bingo-blackjack   37.737609   
41    techcrunch50, tc50, learning, grockit, gmat, m...   37.775196   
1263  gaming, iphone-games, mobile-games, mobile, ip...   37.770510   
1941  iphone, real-world-gaming, location-based-gami...   37.420728   

      office_lon  funds_raised_float currency  fx_rate  funds_raised_usd  \
916  -122.401406                 0.0        $      1.0               0.0   
1070 -122.396744                 0.0        $      1.0               0.0   
1432 -122.438231                 0.0        $      1.0               0.0   
1950 -122.395785           1000000.0        $      1.0         1000000.0   
1500 -122.399972           4000000.0        $      1.0         4000000.0   
99   -122.393229           4800000.0        $      1.0         4800000.0   
2690 -122.435399          16300000.0        $      1.0        16300000.0   
41   -122.419204          44700000.0        $      1.0        44700000.0   
1263 -122.401581          44800000.0        $      1.0        44800000.0   
1941 -122.210341          59500000.0        $      1.0        59500000.0   

      desing_tag  gaming_tag  funding_tag  
916        False        True        False  
1070       False        True        False  
1432       False        True        False  
1950       False        True        False  
1500       False        True         True  
99         False        True         True  
2690       False        True         True  
41         False        True         True  
1263       False        True         True  
1941       False        True         True

plaYce

In [1332]:
comp_df[(comp_df["city"]=="New York")&(comp_df["gaming_tag"]==True)].sort_values("funds_raised_float")

name      city country  \
914                  AdParlor  New York     USA   
1423       Dada Entertainment  New York     USA   
3707                   Zemoga  New York     USA   
3859  FremantleMedia Ventures  New York     USA   
2998             Crispy Gamer  New York     USA   
288                    Boonty  New York     USA   
3568               GameGround  New York     USA   
96                     OMGPOP  New York     USA   
93                  Thumbplay  New York     USA   
2957      Major League Gaming  New York     USA   

                                                   tags  office_lat  \
914   advertising, facebook, advertising-on-facebook...   40.726241   
1423  music, mobile, web-2-0, community, sharing, vi...   40.754300   
3707  colombia, bogota, innovation, social-networkin...   40.744697   
3859  investor, financial-organization, entertainmen...   40.743945   
2998  videogaming, community, editorial, the-game-tr...   40.750597   
288   games, free-online-games, community, social-ca...   40.717248   
3568  achievements, gaming, online-gaming, share, ga...   40.756054   
96                              dating, gaming, auction   40.723384   
93    mobile, music, video, sharing, gaming, cloud, ...   40.725435   
2957  mlg, gaming, halo, competitive, tournament, ga...   40.752672   

      office_lon  funds_raised_float currency  fx_rate  funds_raised_usd  \
914   -74.007327                 0.0        $      1.0               0.0   
1423  -73.981847                 0.0        $      1.0               0.0   
3707  -73.989947                 0.0        $      1.0               0.0   
3859  -73.985542                 0.0        $      1.0               0.0   
2998  -73.985273           8250000.0        $      1.0         8250000.0   
288   -74.002662          10000000.0        $      1.0        10000000.0   
3568  -73.986951          11400000.0        $      1.0        11400000.0   
96    -74.001704          16600000.0        $      1.0        16600000.0   
93    -73.997395          41500000.0        $      1.0        41500000.0   
2957  -73.975930          69000000.0        $      1.0        69000000.0   

      desing_tag  gaming_tag  funding_tag  
914        False        True        False  
1423       False        True        False  
3707       False        True        False  
3859       False        True        False  
2998       False        True         True  
288        False        True         True  
3568       False        True         True  
96         False        True         True  
93         False        True         True  
2957       False        True         True

#Boonty

In [1333]:
def heatmap_top3(location,dataframe,condition_filter):
    map_ = Map(location=location, zoom_start = 12)

    filtered_df =comp_df[condition_filter]
    group = folium.FeatureGroup(name=f"Funding {filtered_df.shape[0]}")

    HeatMap(data = filtered_df[["office_lat", "office_lon"]]).add_to(map_)
    group.add_to(map_)
    return map_

In [1334]:
heatmap_top3([51.500152,-0.126236],comp_df,(comp_df["funds_raised_usd"]>1000000)|(comp_df["desing_tag"]==True)) #LONDON

In [1335]:
heatmap_top3([40.7549309, -73.9840195],comp_df,(comp_df["funds_raised_usd"]>1000000)|(comp_df["desing_tag"]==True)) #NY

In [1336]:
heatmap_top3([37.777720,-122.395785],comp_df,(comp_df["funds_raised_usd"]>1000000)|(comp_df["desing_tag"]==True)) #San Francisco

## Foursquare API

In [1337]:
passwd = os.getenv("passwd")

In [1338]:
def fsq_request(query,lat_lon,radius,category,limit):

    """returns the result for query in radius of x around a specific coordinates"""
    if category != 0:
        url = f"https://api.foursquare.com/v3/places/search?query={query}&ll={lat_lon[0]}%2C{lat_lon[1]}&radius={radius}&categories={category}&limit={limit}"
    elif category == 0:
        url = f"https://api.foursquare.com/v3/places/search?query={query}&ll={lat_lon[0]}%2C{lat_lon[1]}&radius={radius}&limit={limit}"
            
    query = query.replace(" ","%20")


    headers = {
        "accept": "application/json",
        "Authorization": passwd
    }

    response = requests.get(url, headers=headers)

    return response.json()["results"]



## Querying API

In [1339]:
coord_london = [51.500152,-0.126236]
airport_london = fsq_request("airport",coord_london,30000,19040,50)
starbucks_london = fsq_request("starbucks",coord_london,1500,13035,50)
school_london = fsq_request("primary school",coord_london,1500,12057,50)
v_restaurant_london = fsq_request("vegan restaurant",coord_london,1500,13377,50)
night_club_london = fsq_request("night club",coord_london,1500,10032,50)
dog_groom_london = fsq_request("dog hairdresser",coord_london,1500,11134,50)
basketball_london = fsq_request("basketball court",coord_london,1500,18008,50)



In [1340]:
coord_ny = [40.7549309, -73.9840195]
airport_ny = fsq_request("airport",coord_ny,30000,19040,50)
starbucks_ny = fsq_request("starbucks",coord_ny,1500,13035,50)
school_ny= fsq_request("primary school",coord_ny,1500,12057,50)
v_restaurant_ny = fsq_request("vegan restaurant",coord_ny,1500,13377,50)
night_club_ny = fsq_request("night club",coord_ny,1500,10032,50)
dog_groom_ny = fsq_request("dog hairdresser",coord_ny,1500,11134,50)
basketball_ny = fsq_request("basketball court",coord_ny,1500,18008,50)

In [1341]:
coord_sf = [37.777720,-122.395785] 
airport_sf = fsq_request("airport",coord_sf,30000,19040,50)
starbucks_sf = fsq_request("starbucks",coord_sf,1500,13035,50)
school_sf = fsq_request("primary school",coord_sf,1500,12057,50)
v_restaurant_sf = fsq_request("vegan restaurant",coord_sf,1500,13377,50)
night_club_sf = fsq_request("night club",coord_sf,1500,10032,50)
dog_groom_sf = fsq_request("dog hairdresser",coord_sf,1500,11134,50)
basketball_sf = fsq_request("basketball court",coord_sf,1500,18008,50)

In [1342]:
category_code_list = [19040, 13035, 12057, 13377, 10032, 11134, 18008]

## loading mongo

In [1343]:

try:
    london_list = [ airport_london, starbucks_london, school_london, v_restaurant_london, night_club_london, dog_groom_london, basketball_london]
    london_list_flat = [j for i in london_list for j in i ]

    for i in range(len(london_list_flat)):
        london_list_flat[i]["geocodes"]["main"] = dict(collections.OrderedDict(sorted(london_list_flat[i]["geocodes"]["main"].items(),reverse=True)))
        
    with open('data/london_api.json', 'w') as fout:
        json.dump(london_list_flat, fout)

    mycol = db.create_collection("london_places")


    with open("data/london_api.json") as file:
        file_data = json.load(file)
        
    db["london_places"].insert_many(file_data)

    london_places_col = db.get_collection("london_places")
except:
    pass


In [1344]:
try:
    sf_list = [ airport_sf, starbucks_sf, school_sf, v_restaurant_sf, night_club_sf, dog_groom_sf, basketball_sf]
    sf_list_flat = [j for i in sf_list for j in i ]

    for i in range(len(sf_list_flat)):
        sf_list_flat[i]["geocodes"]["main"] = dict(collections.OrderedDict(sorted(sf_list_flat[i]["geocodes"]["main"].items(),reverse=True)))
        
    with open('data/sf_api.json', 'w') as fout:
        json.dump(sf_list_flat, fout)

    mycol = db.create_collection("sf_places")


    with open("data/sf_api.json") as file:
        file_data = json.load(file)
        
    db["sf_places"].insert_many(file_data)

    sf_places_col = db.get_collection("sf_places")
except:
    pass

In [1345]:
try:
    ny_list = [ airport_ny, starbucks_ny, school_ny, v_restaurant_ny, night_club_ny, dog_groom_ny, basketball_ny]
    ny_list_flat = [j for i in ny_list for j in i ]

    for i in range(len(ny_list_flat)):
        ny_list_flat[i]["geocodes"]["main"] = dict(collections.OrderedDict(sorted(ny_list_flat[i]["geocodes"]["main"].items(),reverse=True)))
        
    with open('data/ny_api.json', 'w') as fout:
        json.dump(ny_list_flat, fout)

    mycol = db.create_collection("ny_places")


    with open("data/ny_api.json") as file:
        file_data = json.load(file)
        
    db["ny_places"].insert_many(file_data)

    ny_places_col = db.get_collection("ny_places")
except:
    pass


In [1346]:

# Create indexes in mongo # Done
# Geospacial query (1000 mts) # Done
# get the closest place of each category
# assign value to each requirement and calculate which is the one with the best score
# plot 3 options

## Querying Mongo

In [1347]:
london_places_col = db.get_collection("london_places")
sf_places_col = db.get_collection("sf_places")
ny_places_col = db.get_collection("ny_places")

In [1348]:
def type_point_mongo (list_):
    """ Mongo uses LONGITUDE first, LATITUDE second"""
    list_ = list_[::-1]
    formatted_dict_ = {"type": "Point", "coordinates": list_}
    return formatted_dict_

In [1349]:
def close_by (collection,location, distance):

    converted_location = type_point_mongo(location)
    
    query = {"geocodes.main": 
            {"$near": 
                {"$geometry": converted_location, "$maxDistance": distance
                }}}

    proy_ = {"_id": 0}
    
    result = list(collection.find(query, proy_))
    
    print(len(result))

    return result

In [1350]:
london_places = close_by(london_places_col,coord_london,30000)
sf_places =close_by(sf_places_col,coord_sf,30000)
ny_places =close_by(ny_places_col,coord_ny,30000)

118
96
232


In [1351]:
# had to add category code filter, there are venues with more than 1 category code, which are invalid

category_id = [london_places[i]["categories"][j]["id"] for i in range(len(london_places)) for j in range(len(london_places[i]["categories"])) if london_places[i]["categories"][j]["id"] in category_code_list] 
category_name = [london_places[i]["categories"][j]["name"] for i in range(len(london_places)) for j in range(len(london_places[i]["categories"])) if london_places[i]["categories"][j]["id"] in category_code_list]
distance = [london_places[i]["distance"] for i in range(len(london_places)) for j in range(len(london_places[i]["categories"])) if london_places[i]["categories"][j]["id"] in category_code_list]
lat = [london_places[i]["geocodes"]["main"]["latitude"] for i in range(len(london_places)) for j in range(len(london_places[i]["categories"])) if london_places[i]["categories"][j]["id"] in category_code_list]
lon = [london_places[i]["geocodes"]["main"]["longitude"] for i in range(len(london_places)) for j in range(len(london_places[i]["categories"])) if london_places[i]["categories"][j]["id"] in category_code_list]
name = [london_places[i]["name"] for i in range(len(london_places)) for j in range(len(london_places[i]["categories"])) if london_places[i]["categories"][j]["id"] in category_code_list]

london_dict = {
    "category_id" : category_id,
    "category_name" : category_name,
    "distance": distance,
    "lat" : lat,
    "lon" : lon,
    "name" : name
}

london_df = pd.DataFrame(london_dict)
london_df

category_id                    category_name  distance        lat  \
0         11134             Pet Grooming Service       443  51.500761   
1         13035                      Coffee Shop       495  51.498155   
2         13035                      Coffee Shop       519  51.499091   
3         13035                      Coffee Shop       626  51.502156   
4         13377  Vegan and Vegetarian Restaurant       649  51.496694   
..          ...                              ...       ...        ...   
90        10032                       Night Club      1476  51.513165   
91        13035                      Coffee Shop      1479  51.512795   
92        13035                      Coffee Shop      1493  51.494624   
93        19040            International Airport     12167  51.504029   
94        19040            International Airport     23268  51.470584   

         lon                           name  
0  -0.132576                       Marabese  
1  -0.132786                      Starbucks  
2  -0.133591                      Starbucks  
3  -0.117629                      Starbucks  
4  -0.133948             MAAD - Plant-Based  
..       ...                            ...  
90 -0.131082                         Ku Bar  
91 -0.133230                      Starbucks  
92 -0.145918                      Starbucks  
93  0.049552      London City Airport (LCY)  
94 -0.454958  London Heathrow Airport (LHR)  

[95 rows x 6 columns]

In [1352]:
category_id = [ny_places[i]["categories"][j]["id"] for i in range(len(ny_places)) for j in range(len(ny_places[i]["categories"])) if ny_places[i]["categories"][j]["id"] in category_code_list] 
category_name = [ny_places[i]["categories"][j]["name"] for i in range(len(ny_places)) for j in range(len(ny_places[i]["categories"])) if ny_places[i]["categories"][j]["id"] in category_code_list]
distance = [ny_places[i]["distance"] for i in range(len(ny_places)) for j in range(len(ny_places[i]["categories"])) if ny_places[i]["categories"][j]["id"] in category_code_list]
lat = [ny_places[i]["geocodes"]["main"]["latitude"] for i in range(len(ny_places)) for j in range(len(ny_places[i]["categories"])) if ny_places[i]["categories"][j]["id"] in category_code_list]
lon = [ny_places[i]["geocodes"]["main"]["longitude"] for i in range(len(ny_places)) for j in range(len(ny_places[i]["categories"])) if ny_places[i]["categories"][j]["id"] in category_code_list]
name = [ny_places[i]["name"] for i in range(len(ny_places)) for j in range(len(ny_places[i]["categories"])) if ny_places[i]["categories"][j]["id"] in category_code_list]

ny_dict = {
    "category_id" : category_id,
    "category_name" : category_name,
    "distance": distance,
    "lat" : lat,
    "lon" : lon,
    "name" : name
}

ny_df = pd.DataFrame(ny_dict)
ny_df.sort_values("name")


category_id                    category_name  distance        lat  \
124        13377  Vegan and Vegetarian Restaurant      1115  40.745007   
125        18008                 Basketball Court      1116  40.763603   
127        18008                 Basketball Court      1123  40.763658   
114        10032                       Night Club      1055  40.749319   
191        13377  Vegan and Vegetarian Restaurant      1469  40.759380   
..           ...                              ...       ...        ...   
186        13377  Vegan and Vegetarian Restaurant      1464  40.756761   
110        13377  Vegan and Vegetarian Restaurant      1021  40.746370   
142        10032                       Night Club      1153  40.749329   
146        11134             Pet Grooming Service      1209  40.745053   
145        13377  Vegan and Vegetarian Restaurant      1190  40.759008   

           lon                              name  
124 -73.981998                  31st Street Food  
125 -73.990721                         ABC Hoops  
127 -73.990679  ABC Hoops NYC Midtown West Arena  
114 -73.994134                    Albion Batcave  
191 -73.967226                             Amata  
..         ...                               ...  
186 -73.966785                      Veggie Grill  
110 -73.988380                     Vistro Burger  
142 -73.995750                      Walter's Bar  
146 -73.978287               Walter's Pet Styles  
145 -73.971012                          by CHLOE  

[195 rows x 6 columns]

In [1353]:
category_id = [sf_places[i]["categories"][j]["id"] for i in range(len(sf_places)) for j in range(len(sf_places[i]["categories"])) if sf_places[i]["categories"][j]["id"] in category_code_list] 
category_name = [sf_places[i]["categories"][j]["name"] for i in range(len(sf_places)) for j in range(len(sf_places[i]["categories"])) if sf_places[i]["categories"][j]["id"] in category_code_list]
distance = [sf_places[i]["distance"] for i in range(len(sf_places)) for j in range(len(sf_places[i]["categories"])) if sf_places[i]["categories"][j]["id"] in category_code_list]
lat = [sf_places[i]["geocodes"]["main"]["latitude"] for i in range(len(sf_places)) for j in range(len(sf_places[i]["categories"])) if sf_places[i]["categories"][j]["id"] in category_code_list]
lon = [sf_places[i]["geocodes"]["main"]["longitude"] for i in range(len(sf_places)) for j in range(len(sf_places[i]["categories"])) if sf_places[i]["categories"][j]["id"] in category_code_list]
name = [sf_places[i]["name"] for i in range(len(sf_places)) for j in range(len(sf_places[i]["categories"])) if sf_places[i]["categories"][j]["id"] in category_code_list]

sf_dict = {
    "category_id" : category_id,
    "category_name" : category_name,
    "distance": distance,
    "lat" : lat,
    "lon" : lon,
    "name" : name
}

sf_df = pd.DataFrame(sf_dict)
sf_df.sort_values("name")


category_id                    category_name  distance        lat  \
29        10032                       Night Club       878  37.778128   
40        10032                       Night Club       959  37.778035   
43        10032                       Night Club      1039  37.786428   
20        18008                 Basketball Court       672  37.771896   
48        10032                       Night Club      1133  37.771064   
..          ...                              ...       ...        ...   
74        13377  Vegan and Vegetarian Restaurant      1406  37.781240   
3         10032                       Night Club       229  37.779182   
83        10032                       Night Club      1471  37.767481   
26        10032                       Night Club       853  37.782232   
50        10032                       Night Club      1134  37.785207   

           lon                 name  
29 -122.405784          1015 Folsom  
40 -122.406567          1040 Folsom  
43 -122.400180                Alibi  
20 -122.397532  Arterra Mission Bay  
48 -122.386157   Bay View Boat Club  
..         ...                  ...  
74 -122.411217   The Flying Falafel  
3  -122.397961  The Grand Nightclub  
83 -122.406590   The Great Northern  
26 -122.403804         The Red Room  
50 -122.404625             The View  

[87 rows x 6 columns]

## calculating distance in comp_df

In [1354]:

def haversine(coord1, coord2):
 
    # Coordinates in decimal degrees (e.g. 2.89078, 12.79797)
    lon1, lat1 = coord1
    lon2, lat2 = coord2

    R = 6371000  # radius of Earth in meters
    phi_1 = math.radians(lat1)
    phi_2 = math.radians(lat2)

    delta_phi = math.radians(lat2 - lat1)
    delta_lambda = math.radians(lon2 - lon1)

    a = math.sin(delta_phi / 2.0) ** 2 + math.cos(phi_1) * math.cos(phi_2) * math.sin(delta_lambda / 2.0) ** 2
    
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))

    meters = R * c  # output distance in meters
    km = meters / 1000.0  # output distance in kilometers

    return round(meters, 3)




In [1355]:
comp_df_top3 = comp_df[comp_df["city"].isin(["San Francisco","London","New York"])] #filter top 3
comp_df_top3["category_name"] = comp_df_top3.apply(lambda row: "design/Funding1M" if (row["funding_tag"]==True|row["desing_tag"]==True) else False, axis=1)
comp_df_top3["coord"] =  list(zip(comp_df_top3['office_lat'], comp_df_top3['office_lon'])) #create coord field to calc distance

In [1356]:
comp_df_ny = comp_df_top3[comp_df_top3["city"]=="New York"]
comp_df_london = comp_df_top3[comp_df_top3["city"]=="London"]
comp_df_sf = comp_df_top3[comp_df_top3["city"]=="San Francisco"]

In [1357]:
comp_df_ny["distance"] = comp_df_ny["coord"].apply(lambda x: haversine(coord_ny,x))
comp_df_london["distance"] = comp_df_london["coord"].apply(lambda x: haversine(coord_london,x))
comp_df_sf["distance"] = comp_df_sf["coord"].apply(lambda x: haversine(coord_sf,x))

## Weight of option

Tier 1: 95%

- International Airport
- Primary and Secondary School	
- Vegan and Vegetarian Restaurant	
- 1M comparable companies
- Design companies
- Coffee Shop
- Night Club

Tier 2: 5%
- Pet Grooming Service
- Basketball Court	




In [1358]:
def comp_score(df):

    comp_df =pd.DataFrame({
    "tag":["desing_tag","funding_tag"],
    "min_dist" : [df[df["desing_tag"]==True]["distance"].min(),df[df["funding_tag"]==True]["distance"].min()]
    })

    comp_df["score"] = comp_df["min_dist"]*(0.95/7)
    return comp_df

In [1359]:
comp_score(comp_df_sf)

tag  min_dist       score
0   desing_tag   786.712  106.768057
1  funding_tag   290.976   39.489600

In [1360]:
comp_score(comp_df_ny)

tag  min_dist      score
0   desing_tag   327.784  44.484971
1  funding_tag   146.713  19.911050

In [1361]:
comp_score(comp_df_london)

tag  min_dist     score
0   desing_tag      0.00  0.000000
1  funding_tag      0.05  0.006786

In [1362]:
ny_cat_score = ny_df.groupby(["category_name"])["distance"].min().reset_index()

In [1363]:
sf_cat_score = sf_df.groupby(["category_name"])["distance"].min().reset_index()

In [1364]:
london_cat_score = london_df.groupby(["category_name"])["distance"].min().reset_index()

In [1365]:
def cat_weight(row):
    tier1_cat = ["International Airport" ,"Primary and Secondary School","Vegan and Vegetarian Restaurant","Coffee Shop","Night Club"]
    if row['category_name'] in (tier1_cat):
        return row['distance']*(0.95/7)
    else:
        return row['distance']*(0.05/2)
    

In [1366]:
london_cat_score["score"] = london_cat_score.apply(cat_weight, axis=1)
sf_cat_score["score"] = sf_cat_score.apply(cat_weight, axis=1)
ny_cat_score["score"] = ny_cat_score.apply(cat_weight, axis=1)

In [1367]:
london_cat_score

category_name  distance        score
0                 Basketball Court      1251    31.275000
1                      Coffee Shop       495    67.178571
2            International Airport     12167  1651.235714
3                       Night Club       881   119.564286
4             Pet Grooming Service       443    11.075000
5     Primary and Secondary School      1135   154.035714
6  Vegan and Vegetarian Restaurant       649    88.078571

In [1368]:
sf_cat_score

category_name  distance        score
0                 Basketball Court       672    16.800000
1                      Coffee Shop       189    25.650000
2            International Airport     17613  2390.335714
3                       Night Club       174    23.614286
4             Pet Grooming Service       279     6.975000
5     Primary and Secondary School       505    68.535714
6  Vegan and Vegetarian Restaurant       589    79.935714

In [1369]:
ny_cat_score

category_name  distance        score
0                 Basketball Court       836    20.900000
1                      Coffee Shop       221    29.992857
2            International Airport      9900  1343.571429
3                       Night Club       148    20.085714
4             Pet Grooming Service       687    17.175000
5     Primary and Secondary School       216    29.314286
6  Vegan and Vegetarian Restaurant        44     5.971429

In [1370]:
london_cat_score["score"].sum() + comp_score(comp_df_london)["score"].sum()

2122.449642857143

In [1371]:
sf_cat_score["score"].sum() + comp_score(comp_df_sf)["score"].sum()

2758.1040857142852

In [1372]:
ny_cat_score["score"].sum() + comp_score(comp_df_ny)["score"].sum()

1531.4067357142853

In [1397]:
comp_df_plot = comp_df_top3[["category_name","office_lat","office_lon","name"]][comp_df_top3["category_name"]!=False].rename(columns={"office_lat":"lat","office_lon":"lon"})

In [1398]:
places_df = pd.concat([london_df[["category_name","lat","lon","name"]],sf_df[["category_name","lat","lon","name"]],ny_df[["category_name","lat","lon","name"]],comp_df_plot])

In [1406]:
ny_map = Map(location=[coord_ny[0], coord_ny[1]], zoom_start = 15)



In [1431]:
for index, row in places_df.iterrows():
    
    #1. MARKER without icon
    mark_type = {"location": [row["lat"], row["lon"]], "tooltip": row["category_name"]}
    
    #2. Icon
    if row["category_name"] == 'Pet Grooming Service':        
        icon = Icon (
            color="blue",
            opacity = 0.6,
            prefix = "fa",
            icon="paw",
            icon_color = "white"
        )
    elif row["category_name"] == "Coffee Shop":
        icon = Icon (
            color="white",
            opacity = 0.6,
            prefix = "fa",
            icon="coffee",
            icon_color = "green"
        )
    elif row["category_name"] == "Vegan and Vegetarian Restaurant":
        icon = Icon (
            color="green",
            opacity = 0.6,
            prefix = "fa",
            icon="leaf",
            icon_color = "white"
        )
    elif row["category_name"] == "Night Club":
        icon = Icon (
            color="black",
            opacity = 0.6,
            prefix = "fa",
            icon="beer",
            icon_color = "yellow"
        )
    elif row["category_name"] == "Primary and Secondary School":
        icon = Icon (
            color="darkblue",
            opacity = 0.6,
            prefix = "fa",
            icon="child",
            icon_color = "white"
        )
    elif row["category_name"] == "Basketball Court":
        icon = Icon (
            color="black",
            opacity = 0.6,
            prefix = "fa",
            icon="basketball",
            icon_color = "orange"
        )
    elif row["category_name"] == "International Airport":
        icon = Icon (
            color="red",
            opacity = 0.6,
            prefix = "fa",
            icon="plane",
            icon_color = "white"
        )    
    elif row["category_name"] == "design/Funding1M":
        icon = Icon (
            color="darkpurple",
            opacity = 0.6,
            prefix = "fa",
            icon="briefcase",
            icon_color = "white"
        )
    else:
        icon = Icon (
            color="blue",
            opacity = 0.6,
            prefix = "fa",
            icon="question",
            icon_color = "brown",
            icon_size=(14, 14)
        )
    #3. Marker
    new_marker = Marker(**mark_type, icon = icon, radius = 2)
    
    #4. Add the Marker
    new_marker.add_to(ny_map)

folium.Circle([coord_ny[0], coord_ny[1]], radius=500).add_to(ny_map)
folium.Circle([coord_ny[0], coord_ny[1]], radius=1000).add_to(ny_map)
folium.Circle([coord_ny[0], coord_ny[1]], radius=10000).add_to(ny_map)

In [1432]:
ny_map